# Exercise 11: Shared-State Concurrency

Lets us write a python class that offers some protection against data-race. The idea is to encapsulate a value in a ```MuVar``` object. That object should use a mutex to allow locking and unlocking. It should also check that only the correct thread access the variable.

In [1]:
import threading, time

## API

We present some of the Python API that can be helpful for implementing the exercise.

### Mutex

Mutex in Python are called Lock.

In [2]:
l = threading.RLock()
l.acquire()
print("a")

def thread_function(l):
    with l:
        print("From thread_function")

x = threading.Thread(target=thread_function, args=(l,))
x.start()

time.sleep(2.0)

print("b")
l.release()


a
b
From thread_function


### get_ident

```threading.get_ident()``` returns an identifier that is unique to the current thread

In [3]:
def thread_function(l):
    print("From thread_function", threading.get_ident())

print("Main thread", threading.get_ident())
x = threading.Thread(target=thread_function, args=(l,))
x.start()

Main thread 139775130740544
From thread_function 139774677481216


### with block

To enable support for with block, a class should implement ```__enter__``` and ```__exit__```.

In [4]:
class BlockObject:
    def __enter__(self):
        print("__enter__")
    def __exit__(self, exc_type, exc_value, traceback):
        print("__exit__")

bo = BlockObject()
print("before block")
with bo:
    print("in block")
print("after block")

before block
__enter__
in block
__exit__
after block


## MuVar implementation

You should now complete the ```MuVar``` class so that it provide an implementation with some level of protection against data-race. The idea is that ```MuVar``` encapsulates an object, and should raise an exception when accessing the object without locking and/or from the wrong thread.

In [5]:
class InvalidMuVarAccess(Exception):
    def __init__(self):
        super().__init__("Invalid thread access")

class MuVar:
    def __init__(self,value):
        self.__value = value
        pass
    def __getattr__(self, name):
        """This function is called when looking for a member of an object"""
        return self.__value.__getattribute__(name)
    def __getitem__(self, name):
        """This function is called when using the [] operator"""
        return self.__value.__getitem__(name)
    def __len__(self):
        """This function is called when using len"""
        return len(self.__value)

## Test cases

This test that we can use the variable with the with block in a single thread.

In [6]:
a = MuVar([])
with a:
    a.append(1)
    print(a[0])

AttributeError: __enter__

The following two cells test that accessing the variable without locking it in a block triggers a failure:

In [ ]:
try:
    a.append(1)
    raise Exception("Failure")
except InvalidMuVarAccess:
    print("Success")

In [ ]:
try:
    print(a[0])
    raise Exception("Failure")
except InvalidMuVarAccess:
    print("Success")

This test that locking the variable and then using from a different thread fails:

In [ ]:
def thread_function(a):
    try:
        print(a[0])
        raise Exception("Failure")
    except InvalidMuVarAccess:
        print("Success")
with a:
    x = threading.Thread(target=thread_function, args=(a,))
    x.start()


This tests that accessing the variable with the proper with statement works:

In [ ]:
def thread_function(a):
    with a:
        print(a[0])

with a:
    x = threading.Thread(target=thread_function, args=(a,))
    x.start()


This test that he variable is properly locked:

In [ ]:
def thread_function(a):
    with a:
        a.append(0)

with a:
    la = len(a)
    x = threading.Thread(target=thread_function, args=(a,))
    x.start()
    time.sleep(2.0)
    assert(la == len(a))

## Question

While ```MuVar``` offers some level of protection. Can you think of at least two issues with the implementation that would allow a developer to go around the data race protection?

***Answer goes here***